In [1]:
import pandas as pd
import numpy as np
import os

from nltk.stem.porter import PorterStemmer
from textVectorizer import *

In [16]:
directories = []
docs = []
for filename in os.listdir("data/C50test"):
    directories.append(filename)
for dir in directories:
    for doc in os.listdir("data/C50test/" + dir):
        docs.append('/'.join(['data', 'C50test', dir, doc]))
sampdocs = pd.Series(docs).sample(25)
sampdocs

1115     data/C50test/LynneO'Donnell/480355newsML.txt
1335       data/C50test/MatthewBunce/458645newsML.txt
1674         data/C50test/RobinSidel/270064newsML.txt
571        data/C50test/JohnMastrini/318112newsML.txt
196         data/C50test/EricAuchard/418918newsML.txt
95          data/C50test/DavidLawder/288662newsML.txt
679      data/C50test/JoWinterbottom/253045newsML.txt
1664         data/C50test/PierreTran/576483newsML.txt
887        data/C50test/KevinMorrison/38625newsML.txt
1858       data/C50test/SarahDavison/677538newsML.txt
2055      data/C50test/TheresePoletti/42990newsML.txt
1400      data/C50test/MichaelConnor/540454newsML.txt
664        data/C50test/JonathanBirt/510819newsML.txt
1443          data/C50test/MureDickie/29645newsML.txt
1212    data/C50test/MarcelMichelson/351919newsML.txt
886        data/C50test/KevinMorrison/38618newsML.txt
177         data/C50test/EricAuchard/337934newsML.txt
1869        data/C50test/ScottHillis/349276newsML.txt
422          data/C50test/Ja

In [130]:
def get_filenames(homedir, size = None):
    directories, docs = [], []
    for filename in os.listdir(homedir):
        directories.append(filename)
    for d in directories:
        for doc in os.listdir(homedir + '/' + d):
            docs.append('/'.join([homedir, d, doc]))
    docs = pd.Series(docs)
    if size is not None:
        docs = docs.sample(size)
    return docs

In [131]:
get_filenames("data/C50train", 25)

269           data/C50train/BradDorfman/231427newsML.txt
1077            data/C50train/KeithWeir/181588newsML.txt
1405      data/C50train/LynnleyBrowning/116673newsML.txt
812              data/C50train/JoeOrtiz/186895newsML.txt
1527         data/C50train/MarkBendeich/294969newsML.txt
1438      data/C50train/LynnleyBrowning/269386newsML.txt
318      data/C50train/DarrenSchuettler/168489newsML.txt
743             data/C50train/JanLopatka/27569newsML.txt
1388       data/C50train/LynneO'Donnell/238772newsML.txt
2292              data/C50train/TanEeLyn/41230newsML.txt
24          data/C50train/AaronPressman/270346newsML.txt
1953           data/C50train/RobinSidel/110827newsML.txt
672         data/C50train/JaneMacartney/162404newsML.txt
755           data/C50train/JimGilchrist/11269newsML.txt
2124         data/C50train/SarahDavison/324597newsML.txt
154       data/C50train/BenjaminKangLim/114204newsML.txt
1266    data/C50train/KouroshKarimkhany/167199newsML.txt
944          data/C50train/Jona

In [136]:
all_lines = []
for doc in sampdocs:
    with open(doc, 'r') as doctxt:
        lines = [line.strip('\n') for line in doctxt.readlines()]
        all_lines.extend(lines)
words_step1 = pd.Series(pd.Series(all_lines).str.lower().str.replace(r"[^a-zA-Z'.]|^\.|\.$", ' ', regex=True).str.split().explode().str.replace(r"^'|'$|'s$|\.", '', regex=True).str.strip(" ").unique()).sort_values()
words_step1

315               
47               a
443        abidjan
130           able
2324    abolishing
           ...    
1797        youths
1402       zealand
1635         zemin
246        zhuzhou
148           zinc
Length: 2812, dtype: object

In [94]:
stopwords = pd.read_csv('https://users.csc.calpoly.edu/~dekhtyar/466-Fall2023/labs/lab6/stopwords-long.txt', header=None, sep=" ")[0]
words_step2 = words_step1[(~words_step1.isin(stopwords)) & (words_step1.str.len() > 0)]
words_step2

442        abidjan
2325    abolishing
2162       absence
1841    absolutely
2323     abstained
           ...    
1797        youths
1402       zealand
1635         zemin
246        zhuzhou
148           zinc
Length: 2454, dtype: object

In [95]:
p = PorterStemmer()
words_step3 = words_step2.apply(lambda w: p.stem(w, 0, len(w)-1)).unique()
words_step3

array(['abidjan', 'abolish', 'absenc', ..., 'zemin', 'zhuzhou', 'zinc'],
      dtype=object)

In [274]:
def get_stopwords(link):
    return pd.read_csv(link, header=None, sep=" ")[0]

In [282]:
def get_stemwords(docs, stopwords = get_stopwords('https://users.csc.calpoly.edu/~dekhtyar/466-Fall2023/labs/lab6/stopwords-long.txt')):
    all_lines = []
    for doc in docs:
        with open(doc, 'r') as doctxt:
            lines = [line.strip('\n') for line in doctxt.readlines()]
            all_lines.extend(lines)
    words_step1 = pd.Series(pd.Series(all_lines)
                            .str.lower()
                            .str.replace(r"[^a-zA-Z'.]|^\.|\.$", ' ', regex=True)
                            .str.split()
                            .explode()
                            .str.replace(r"^'|'$|'s$|\.", '', regex=True)
                            .str.strip(" ")
                            .unique()
                            ).sort_values()
    words_step2 = words_step1[(~words_step1.isin(stopwords)) & (words_step1.str.len() > 0)]
    p = PorterStemmer()
    words_step3 = words_step2.apply(lambda w: p.stem(w, 0, len(w)-1)).unique()
    return words_step3

In [284]:
get_stemwords(get_filenames("data/C50train", 25))

array(['abandon', 'abat', 'abbott', ..., 'ziprasidon', 'zovirax',
       'zyprexa'], dtype=object)

In [79]:
def read_doc(s):
    with open(s, 'r') as doctext:
        return doctext.read()

In [117]:
def stem_doc(s):
    p = PorterStemmer()
    return " ".join(pd.Series([s]).str.lower().str.replace(r"[^a-zA-Z'.]|^\.|\.$", ' ', regex=True).str.split().explode().str.replace(r"^'|'$|'s$|\.", '', regex=True).str.strip(" ").apply(lambda w: p.stem(w, 0, len(w)-1)))

In [118]:
doctexts = sampdocs.apply(read_doc).apply(stem_doc)
doctexts

1115    far east metal trader said on tuesdai thei wer...
1335    ivori coast mid crop cocoa harvest is set to e...
1674    the bid war for conrail inc appear to be draw ...
571     seven year after the velvet revolut over commu...
196     share of com corp and us robot corp slid on mo...
95      chrysler corp said mondai it ha develop a new ...
679     electr gener scottish hydro electr plc turn in...
1664    a bid by conglomer lagarder for militari elect...
887     demand for cheaper telephon servic by busi wou...
1858    taiwan ha step forward in the delic run up to ...
2055    intern busi machin corp tuesdai introduc it ne...
1400    first joe camel won a repriev and now the marl...
664     the soar valu of british medic devic compani b...
1443    china on tuesdai slam washington for pursu a p...
1212    french conglomer general de eaux look set to e...
886     apec minist agre on fridai on further trade an...
177     intern busi machin corp gave it stock a cosmet...
1869    the be

In [138]:
tf = pd.DataFrame()
tf['docname'] = sampdocs
tf['fulltext'] = doctexts
for word in words_step3:
    tf[word] = doctexts.str.count(word)
    tf = tf.copy()
tf

docname  \
1115   data/C50test/LynneO'Donnell/480355newsML.txt   
1335     data/C50test/MatthewBunce/458645newsML.txt   
1674       data/C50test/RobinSidel/270064newsML.txt   
571      data/C50test/JohnMastrini/318112newsML.txt   
196       data/C50test/EricAuchard/418918newsML.txt   
95        data/C50test/DavidLawder/288662newsML.txt   
679    data/C50test/JoWinterbottom/253045newsML.txt   
1664       data/C50test/PierreTran/576483newsML.txt   
887      data/C50test/KevinMorrison/38625newsML.txt   
1858     data/C50test/SarahDavison/677538newsML.txt   
2055    data/C50test/TheresePoletti/42990newsML.txt   
1400    data/C50test/MichaelConnor/540454newsML.txt   
664      data/C50test/JonathanBirt/510819newsML.txt   
1443        data/C50test/MureDickie/29645newsML.txt   
1212  data/C50test/MarcelMichelson/351919newsML.txt   
886      data/C50test/KevinMorrison/38618newsML.txt   
177       data/C50test/EricAuchard/337934newsML.txt   
1869      data/C50test/ScottHillis/349276newsML.txt   
422        data/C50test/JanLopatka/320889newsML.txt   
485      data/C50test/JimGilchrist/252104newsML.txt   
1633       data/C50test/PierreTran/434457newsML.txt   
1872      data/C50test/ScottHillis/349325newsML.txt   
487      data/C50test/JimGilchrist/252143newsML.txt   
1113   data/C50test/LynneO'Donnell/470975newsML.txt   
1209  data/C50test/MarcelMichelson/351515newsML.txt   

                                               fulltext  abidjan  abolish  \
1115  far east metal trader said on tuesdai thei wer...        0        0   
1335  ivori coast mid crop cocoa harvest is set to e...        1        0   
1674  the bid war for conrail inc appear to be draw ...        0        0   
571   seven year after the velvet revolut over commu...        0        0   
196   share of com corp and us robot corp slid on mo...        0        0   
95    chrysler corp said mondai it ha develop a new ...        0        0   
679   electr gener scottish hydro electr plc turn in...        0        0   
1664  a bid by conglomer lagarder for militari elect...        0        0   
887   demand for cheaper telephon servic by busi wou...        0        0   
1858  taiwan ha step forward in the delic run up to ...        0        0   
2055  intern busi machin corp tuesdai introduc it ne...        0        0   
1400  first joe camel won a repriev and now the marl...        0        0   
664   the soar valu of british medic devic compani b...        0        0   
1443  china on tuesdai slam washington for pursu a p...        0        0   
1212  french conglomer general de eaux look set to e...        0        0   
886   apec minist agre on fridai on further trade an...        0        0   
177   intern busi machin corp gave it stock a cosmet...        0        0   
1869  the beij appoint committe handl hong kong retu...        0        1   
422   the agricultur ministri said on tuesdai it pla...        0        0   
485   a campaign is be launch to recruit hong kong w...        0        0   
1633  the french govern said tuesdai it wa readi to ...        0        0   
1872  negoti from china and the unit state resum las...        0        0   
487   hong kong air cargo termin ltd hactl is busi h...        0        0   
1113  a plan by us car giant ford motor co to increa...        0        0   
1209  french conglomer general de eaux look set to e...        0        0   

      absenc  absolut  abstain  abus  accept  access  ...  yamaichi  year  \
1115       0        0        0     0       0       0  ...         0     5   
1335       0        0        0     0       0       0  ...         0     7   
1674       0        0        0     0       0       0  ...         0     0   
571        0        0        0     0       0       0  ...         0     2   
196        0        0        0     0       0       0  ...         0     1   
95         0        0        0     0       0       0  ...         0     2   
679        0        0        0     0       0       0  ...         0    

In [139]:
df = tf.set_index('docname').drop('fulltext', axis=1).apply(lambda x: 1 * (x > 0)).sum(axis=0)
n = len(tf['docname'])
idf = np.log2(n / df)
idf

abidjan    4.643856
abolish    4.643856
absenc     4.643856
absolut    4.643856
abstain    4.643856
             ...   
youth      4.643856
zealand    3.643856
zemin      4.643856
zhuzhou    4.643856
zinc       4.643856
Length: 1923, dtype: float64

In [153]:
tf_idf = tf.copy()
tf_idf.iloc[:, 2:] = tf_idf.iloc[:, 2:].add(idf, axis=1)
tf_idf

docname  \
1115   data/C50test/LynneO'Donnell/480355newsML.txt   
1335     data/C50test/MatthewBunce/458645newsML.txt   
1674       data/C50test/RobinSidel/270064newsML.txt   
571      data/C50test/JohnMastrini/318112newsML.txt   
196       data/C50test/EricAuchard/418918newsML.txt   
95        data/C50test/DavidLawder/288662newsML.txt   
679    data/C50test/JoWinterbottom/253045newsML.txt   
1664       data/C50test/PierreTran/576483newsML.txt   
887      data/C50test/KevinMorrison/38625newsML.txt   
1858     data/C50test/SarahDavison/677538newsML.txt   
2055    data/C50test/TheresePoletti/42990newsML.txt   
1400    data/C50test/MichaelConnor/540454newsML.txt   
664      data/C50test/JonathanBirt/510819newsML.txt   
1443        data/C50test/MureDickie/29645newsML.txt   
1212  data/C50test/MarcelMichelson/351919newsML.txt   
886      data/C50test/KevinMorrison/38618newsML.txt   
177       data/C50test/EricAuchard/337934newsML.txt   
1869      data/C50test/ScottHillis/349276newsML.txt   
422        data/C50test/JanLopatka/320889newsML.txt   
485      data/C50test/JimGilchrist/252104newsML.txt   
1633       data/C50test/PierreTran/434457newsML.txt   
1872      data/C50test/ScottHillis/349325newsML.txt   
487      data/C50test/JimGilchrist/252143newsML.txt   
1113   data/C50test/LynneO'Donnell/470975newsML.txt   
1209  data/C50test/MarcelMichelson/351515newsML.txt   

                                               fulltext   abidjan   abolish  \
1115  far east metal trader said on tuesdai thei wer...  4.643856  4.643856   
1335  ivori coast mid crop cocoa harvest is set to e...  5.643856  4.643856   
1674  the bid war for conrail inc appear to be draw ...  4.643856  4.643856   
571   seven year after the velvet revolut over commu...  4.643856  4.643856   
196   share of com corp and us robot corp slid on mo...  4.643856  4.643856   
95    chrysler corp said mondai it ha develop a new ...  4.643856  4.643856   
679   electr gener scottish hydro electr plc turn in...  4.643856  4.643856   
1664  a bid by conglomer lagarder for militari elect...  4.643856  4.643856   
887   demand for cheaper telephon servic by busi wou...  4.643856  4.643856   
1858  taiwan ha step forward in the delic run up to ...  4.643856  4.643856   
2055  intern busi machin corp tuesdai introduc it ne...  4.643856  4.643856   
1400  first joe camel won a repriev and now the marl...  4.643856  4.643856   
664   the soar valu of british medic devic compani b...  4.643856  4.643856   
1443  china on tuesdai slam washington for pursu a p...  4.643856  4.643856   
1212  french conglomer general de eaux look set to e...  4.643856  4.643856   
886   apec minist agre on fridai on further trade an...  4.643856  4.643856   
177   intern busi machin corp gave it stock a cosmet...  4.643856  4.643856   
1869  the beij appoint committe handl hong kong retu...  4.643856  5.643856   
422   the agricultur ministri said on tuesdai it pla...  4.643856  4.643856   
485   a campaign is be launch to recruit hong kong w...  4.643856  4.643856   
1633  the french govern said tuesdai it wa readi to ...  4.643856  4.643856   
1872  negoti from china and the unit state resum las...  4.643856  4.643856   
487   hong kong air cargo termin ltd hactl is busi h...  4.643856  4.643856   
1113  a plan by us car giant ford motor co to increa...  4.643856  4.643856   
1209  french conglomer general de eaux look set to e...  4.643856  4.643856   

        absenc   absolut   abstain      abus    accept    access  ...  \
1115  4.643856  4.643856  4.643856  4.643856  3.058894  2.643856  ...   
1335  4.643856  4.643856  4.643856  4.643856  3.058894  2.643856  ...   
1674  4.643856  4.643856  4.643856  4.643856  3.058894  2.643856  ...   
571   4.643856  4.643856  4.643856  4.643856  3.058894  2.643856  ...   
196   4.643856  4.643856  4.643856  4.643856  3.058894  2.643856  ...   
95    4.643856  4.643856  4.643856  4.643856  3.058894  2.643856  ...   
679   4.643856  4.643856  4.643856  4.643856  3

In [180]:
def term_freq(docs, words):
    doctexts = docs.apply(read_doc).apply(stem_doc)

    f = pd.DataFrame()
    f['docname'] = docs
    for word in words:
        f[word] = doctexts.str.count(word)
        f = f.copy()

    return f.set_index('docname')

In [215]:
def norm_term_freq(docs, words, f = None):
    if f is None:
        f = term_freq(docs, words)
    return f.divide(f.max(axis=1), axis=0)

In [191]:
def doc_freq(docs, words, f = None):
    if f is None:
        f = term_freq(docs, words)
    df = f.apply(lambda x: 1 * (x > 0)).sum(axis=0)
    return df

In [268]:
def tf_idf(docs, words, n = None,
           f = None, tf = None, df = None, idf = None,
           query = False):
    if f is None and tf is None:
        f = term_freq(docs, words)
    if tf is None:
        tf = norm_term_freq(docs, words, f=f)

    if df is None and idf is None:
        df = doc_freq(docs, words, f=f)
    if n is None and idf is None:
        n = len(tf.index)
    if idf is None:
        idf = np.log2(n / df)

    if query:
        tf_idf = (0.5 + 0.5*tf).multiply(idf, axis=1)
    else:
        tf_idf = tf.multiply(idf, axis=1)
    return tf_idf

In [295]:
class Corpus:
    def __init__(self, homedir, size = None,
                 stopwords = get_stopwords('https://users.csc.calpoly.edu/~dekhtyar/466-Fall2023/labs/lab6/stopwords-long.txt')):
        self.loc = homedir
        self.docs = get_filenames(homedir, size=size)
        self.words = get_stemwords(self.docs, stopwords=stopwords)
        self.stopwords = stopwords
        self.n = len(self.docs)
        self.df = doc_freq(self.docs, self.words)
        self.idf = np.log2(self.n / self.df)
        self.avdl = self.docs.apply(os.path.getsize).mean()

    def __repr__(self):
        return f"Corpus({self.loc})"

    def remove_doc(self, doc):
        if doc in list(self.docs):
            self.docs = self.docs[~self.docs.isin([doc])]
            self.words = get_stemwords(self.docs, stopwords=self.stopwords)
            self.n = len(self.docs)
            self.df = doc_freq(self.docs, self.words)
            self.idf = np.log2(self.n / self.df)
            self.avdl = self.docs.apply(os.path.getsize).mean()


In [304]:
class Vector:
    def __init__(self, doc, corpus, query = False):
        self.corpus = corpus
        self.query = query

        if self.query is True and doc in list(self.corpus.docs):
            self.corpus.remove_doc(doc)
        doc_srs = pd.Series([doc])

        self.words = self.corpus.words
        self.loc = doc
        f = term_freq(doc_srs, self.words)
        self.f = f.iloc[0]
        tf = norm_term_freq(doc_srs, self.words, f=f)
        self.tf = tf.iloc[0]

        self.df = self.corpus.df
        self.idf = self.corpus.idf
        self.n = self.corpus.n
        self.dl = os.path.getsize(doc)
        self.avdl = self.corpus.avdl

        self.tf_idf = tf_idf(doc_srs, self.corpus.words, tf=tf, idf=self.idf, query=self.query).iloc[0]

    def __repr__(self):
        return f"Vector({self.loc}, corpus={self.corpus.loc}, query={self.query})"

    def cos_sim(self, other):
        a = self.tf_idf
        b = other.tf_idf

        t = list(set(self.f[self.f != 0].index).intersection(set(other.f[other.f != 0].index)))
        a = a.loc[t]
        b = b.loc[t]

        return (a * b).sum() / (np.sqrt((a**2).sum() * (b**2).sum()))

    def okapi(self, other, k1 = 1, k2 = 1):
        if k1 < 1 or k1 > 2:
            raise ValueError("k1 must be in range [1.0, 2.0]")
        if k2 <1 or k2 > 1000:
            raise ValueError("k2 must be in range [1, 1000]")

        b = 0.75
        t = list(set(self.f[self.f != 0].index).intersection(set(other.f[other.f != 0].index)))

        part1 = np.log((n - self.df.loc[t] + 0.5) / (self.df.loc[t] + 0.5))
        part2 = ((k1 + 1) * self.f.loc[t]) / (k1 * (1 - b + b * (self.dl / self.avdl)) + self.f.loc[t])
        part3 = ((k2 + 1) * other.f.loc[t]) / (k2 + other.f.loc[t])

        return (part1 * part2 * part3).sum()

In [170]:
temp = get_filenames("data/C50train", 25)
temp_words = get_stemwords(temp)
tf_idf = tf_idf(temp, temp_words)
tf_idf

abandon      abat   abidjan  \
docname                                                                        
data/C50train/KarlPenhaul/217081newsML.txt      3.058894  4.643856  3.643856   
data/C50train/JoWinterbottom/210506newsML.txt   3.058894  4.643856  3.643856   
data/C50train/MatthewBunce/107670newsML.txt     3.058894  4.643856  4.643856   
data/C50train/BenjaminKangLim/222816newsML.txt  4.058894  4.643856  3.643856   
data/C50train/FumikoFujisaki/167905newsML.txt   3.058894  4.643856  3.643856   
data/C50train/MarcelMichelson/108487newsML.txt  3.058894  4.643856  3.643856   
data/C50train/BradDorfman/321585newsML.txt      3.058894  4.643856  3.643856   
data/C50train/GrahamEarnshaw/244929newsML.txt   3.058894  4.643856  3.643856   
data/C50train/LynneO'Donnell/27316newsML.txt    3.058894  4.643856  3.643856   
data/C50train/JanLopatka/254538newsML.txt       3.058894  4.643856  3.643856   
data/C50train/LynnleyBrowning/308394newsML.txt  3.058894  4.643856  3.643856   
data/C50train/PeterHumphrey/26410newsML.txt     3.058894  4.643856  3.643856   
data/C50train/SimonCowell/15627newsML.txt       4.058894  4.643856  3.643856   
data/C50train/NickLouth/133736newsML.txt        3.058894  4.643856  3.643856   
data/C50train/EdnaFernandes/17343newsML.txt     3.058894  4.643856  3.643856   
data/C50train/MatthewBunce/280201newsML.txt     3.058894  4.643856  7.643856   
data/C50train/WilliamKazer/208244newsML.txt     3.058894  4.643856  3.643856   
data/C50train/MarkBendeich/398974newsML.txt     4.058894  4.643856  3.643856   
data/C50train/TheresePoletti/243514newsML.txt   3.058894  4.643856  3.643856   
data/C50train/EricAuchard/139624newsML.txt      3.058894  4.643856  3.643856   
data/C50train/SarahDavison/213002newsML.txt     3.058894  5.643856  3.643856   
data/C50train/LynnleyBrowning/153131newsML.txt  3.058894  4.643856  3.643856   
data/C50train/PatriciaCommins/108222newsML.txt  3.058894  4.643856  3.643856   
data/C50train/BernardHickey/118470newsML.txt    3.058894  4.643856  3.643856   
data/C50train/PatriciaCommins/117099newsML.txt  3.058894  4.643856  3.643856   

                                                  abnorm    abroad  abruptli  \
docname                                                                        
data/C50train/KarlPenhaul/217081newsML.txt      4.643856  4.643856  4.643856   
data/C50train/JoWinterbottom/210506newsML.txt   4.643856  4.643856  4.643856   
data/C50train/MatthewBunce/107670newsML.txt     4.643856  4.643856  4.643856   
data/C50train/BenjaminKangLim/222816newsML.txt  4.643856  4.643856  4.643856   
data/C50train/FumikoFujisaki/167905newsML.txt   4.643856  4.643856  4.643856   
data/C50train/MarcelMichelson/108487newsML.txt  4.643856  4.643856  4.643856   
data/C50train/BradDorfman/321585newsML.txt      4.643856  4.643856  4.643856   
data/C50train/GrahamEarnshaw/244929newsML.txt   4.643856  4.643856  4.643856   
data/C50train/LynneO'Donnell/27316newsML.txt    4.643856  4.643856  4.643856   
data/C50train/JanLopatka/254538newsML.txt       4.643856  4.643856  4.643856   
data/C50train/LynnleyBrowning/308394newsML.txt  4.643856  4.643856  4.643856   
data/C50train/PeterHumphrey/26410newsML.txt     4.643856  4.643856  4.643856   
data/C50train/SimonCowell/15627newsML.txt       4.643856  4.643856  4.643856   
data/C50train/NickLouth/133736newsML.txt        4.643856  4.643856  4.643856   
data/C50train/EdnaFernandes/17343newsML.txt     4.643856  4.643856  4.643856   
data/C50train/MatthewBunce/280201newsML.txt     4.643856  4.643856  5.643856   
data/C50train/WilliamKazer/208244newsML.txt     4.643856  4.643856  4.643856   
data/C50train/MarkBendeich/398974newsML.txt     6.643856  4.643856  4.643856   
data/C50train/TheresePoletti/243514newsML.txt   4.643856  4.643856  4.643856   
data/C50train/EricAuchard/139624newsML.txt      4.643856  4.643856  4.643856   
data/C50train/SarahDavison/213002newsML.txt     4.643856  4.643856  4.643856   
data/C50train/LynnleyBrowning/153131newsML.txt  

In [183]:
tf = term_freq(temp, temp_words)
tf

abandon  abat  abidjan  \
docname                                                                  
data/C50train/KarlPenhaul/217081newsML.txt            0     0        0   
data/C50train/JoWinterbottom/210506newsML.txt         0     0        0   
data/C50train/MatthewBunce/107670newsML.txt           0     0        1   
data/C50train/BenjaminKangLim/222816newsML.txt        1     0        0   
data/C50train/FumikoFujisaki/167905newsML.txt         0     0        0   
data/C50train/MarcelMichelson/108487newsML.txt        0     0        0   
data/C50train/BradDorfman/321585newsML.txt            0     0        0   
data/C50train/GrahamEarnshaw/244929newsML.txt         0     0        0   
data/C50train/LynneO'Donnell/27316newsML.txt          0     0        0   
data/C50train/JanLopatka/254538newsML.txt             0     0        0   
data/C50train/LynnleyBrowning/308394newsML.txt        0     0        0   
data/C50train/PeterHumphrey/26410newsML.txt           0     0        0   
data/C50train/SimonCowell/15627newsML.txt             1     0        0   
data/C50train/NickLouth/133736newsML.txt              0     0        0   
data/C50train/EdnaFernandes/17343newsML.txt           0     0        0   
data/C50train/MatthewBunce/280201newsML.txt           0     0        4   
data/C50train/WilliamKazer/208244newsML.txt           0     0        0   
data/C50train/MarkBendeich/398974newsML.txt           1     0        0   
data/C50train/TheresePoletti/243514newsML.txt         0     0        0   
data/C50train/EricAuchard/139624newsML.txt            0     0        0   
data/C50train/SarahDavison/213002newsML.txt           0     1        0   
data/C50train/LynnleyBrowning/153131newsML.txt        0     0        0   
data/C50train/PatriciaCommins/108222newsML.txt        0     0        0   
data/C50train/BernardHickey/118470newsML.txt          0     0        0   
data/C50train/PatriciaCommins/117099newsML.txt        0     0        0   

                                                abnorm  abroad  abruptli  \
docname                                                                    
data/C50train/KarlPenhaul/217081newsML.txt           0       0         0   
data/C50train/JoWinterbottom/210506newsML.txt        0       0         0   
data/C50train/MatthewBunce/107670newsML.txt          0       0         0   
data/C50train/BenjaminKangLim/222816newsML.txt       0       0         0   
data/C50train/FumikoFujisaki/167905newsML.txt        0       0         0   
data/C50train/MarcelMichelson/108487newsML.txt       0       0         0   
data/C50train/BradDorfman/321585newsML.txt           0       0         0   
data/C50train/GrahamEarnshaw/244929newsML.txt        0       0         0   
data/C50train/LynneO'Donnell/27316newsML.txt         0       0         0   
data/C50train/JanLopatka/254538newsML.txt            0       0         0   
data/C50train/LynnleyBrowning/308394newsML.txt       0       0         0   
data/C50train/PeterHumphrey/26410newsML.txt          0       0         0   
data/C50train/SimonCowell/15627newsML.txt            0       0         0   
data/C50train/NickLouth/133736newsML.txt             0       0         0   
data/C50train/EdnaFernandes/17343newsML.txt          0       0         0   
data/C50train/MatthewBunce/280201newsML.txt          0       0         1   
data/C50train/WilliamKazer/208244newsML.txt          0       0         0   
data/C50train/MarkBendeich/398974newsML.txt          2       0         0   
data/C50train/TheresePoletti/243514newsML.txt        0       0         0   
data/C50train/EricAuchard/139624newsML.txt           0       0         0   
data/C50train/SarahDavison/213002newsML.txt          0       0         0   
data/C50train/LynnleyBrowning/153131newsML.txt       0       1         0   
data/C50train/PatriciaCommins/108222newsML.txt       0       0         0   
data/C50train/BernardHickey/118470newsML.txt         0       0         0   
data/C50train/PatriciaCommins/117099newsML.txt       0       0         0 

In [214]:
tf.divide(tf.max(axis=1), axis=0)

abandon      abat   abidjan  \
docname                                                                        
data/C50train/KarlPenhaul/217081newsML.txt      0.000000  0.000000  0.000000   
data/C50train/JoWinterbottom/210506newsML.txt   0.000000  0.000000  0.000000   
data/C50train/MatthewBunce/107670newsML.txt     0.000000  0.000000  0.027027   
data/C50train/BenjaminKangLim/222816newsML.txt  0.043478  0.000000  0.000000   
data/C50train/FumikoFujisaki/167905newsML.txt   0.000000  0.000000  0.000000   
data/C50train/MarcelMichelson/108487newsML.txt  0.000000  0.000000  0.000000   
data/C50train/BradDorfman/321585newsML.txt      0.000000  0.000000  0.000000   
data/C50train/GrahamEarnshaw/244929newsML.txt   0.000000  0.000000  0.000000   
data/C50train/LynneO'Donnell/27316newsML.txt    0.000000  0.000000  0.000000   
data/C50train/JanLopatka/254538newsML.txt       0.000000  0.000000  0.000000   
data/C50train/LynnleyBrowning/308394newsML.txt  0.000000  0.000000  0.000000   
data/C50train/PeterHumphrey/26410newsML.txt     0.000000  0.000000  0.000000   
data/C50train/SimonCowell/15627newsML.txt       0.029412  0.000000  0.000000   
data/C50train/NickLouth/133736newsML.txt        0.000000  0.000000  0.000000   
data/C50train/EdnaFernandes/17343newsML.txt     0.000000  0.000000  0.000000   
data/C50train/MatthewBunce/280201newsML.txt     0.000000  0.000000  0.190476   
data/C50train/WilliamKazer/208244newsML.txt     0.000000  0.000000  0.000000   
data/C50train/MarkBendeich/398974newsML.txt     0.030303  0.000000  0.000000   
data/C50train/TheresePoletti/243514newsML.txt   0.000000  0.000000  0.000000   
data/C50train/EricAuchard/139624newsML.txt      0.000000  0.000000  0.000000   
data/C50train/SarahDavison/213002newsML.txt     0.000000  0.032258  0.000000   
data/C50train/LynnleyBrowning/153131newsML.txt  0.000000  0.000000  0.000000   
data/C50train/PatriciaCommins/108222newsML.txt  0.000000  0.000000  0.000000   
data/C50train/BernardHickey/118470newsML.txt    0.000000  0.000000  0.000000   
data/C50train/PatriciaCommins/117099newsML.txt  0.000000  0.000000  0.000000   

                                                  abnorm    abroad  abruptli  \
docname                                                                        
data/C50train/KarlPenhaul/217081newsML.txt      0.000000  0.000000  0.000000   
data/C50train/JoWinterbottom/210506newsML.txt   0.000000  0.000000  0.000000   
data/C50train/MatthewBunce/107670newsML.txt     0.000000  0.000000  0.000000   
data/C50train/BenjaminKangLim/222816newsML.txt  0.000000  0.000000  0.000000   
data/C50train/FumikoFujisaki/167905newsML.txt   0.000000  0.000000  0.000000   
data/C50train/MarcelMichelson/108487newsML.txt  0.000000  0.000000  0.000000   
data/C50train/BradDorfman/321585newsML.txt      0.000000  0.000000  0.000000   
data/C50train/GrahamEarnshaw/244929newsML.txt   0.000000  0.000000  0.000000   
data/C50train/LynneO'Donnell/27316newsML.txt    0.000000  0.000000  0.000000   
data/C50train/JanLopatka/254538newsML.txt       0.000000  0.000000  0.000000   
data/C50train/LynnleyBrowning/308394newsML.txt  0.000000  0.000000  0.000000   
data/C50train/PeterHumphrey/26410newsML.txt     0.000000  0.000000  0.000000   
data/C50train/SimonCowell/15627newsML.txt       0.000000  0.000000  0.000000   
data/C50train/NickLouth/133736newsML.txt        0.000000  0.000000  0.000000   
data/C50train/EdnaFernandes/17343newsML.txt     0.000000  0.000000  0.000000   
data/C50train/MatthewBunce/280201newsML.txt     0.000000  0.000000  0.047619   
data/C50train/WilliamKazer/208244newsML.txt     0.000000  0.000000  0.000000   
data/C50train/MarkBendeich/398974newsML.txt     0.060606  0.000000  0.000000   
data/C50train/TheresePoletti/243514newsML.txt   0.000000  0.000000  0.000000   
data/C50train/EricAuchard/139624newsML.txt      0.000000  0.000000  0.000000   
data/C50train/SarahDavison/213002newsML.txt     0.000000  0.000000  0.000000   
data/C50train/LynnleyBrowning/153131newsML.txt  

In [285]:
corp = Corpus("data/C50test", 25)

In [305]:
vec = Vector(corp.docs.iloc[0], corp)
vec

Vector(data/C50test/EdnaFernandes/343315newsML.txt, corpus=data/C50test, query=False)

In [209]:
os.path.getsize("data/C50test/JoWinterbottom/294369newsML.txt")

3055

In [307]:
query_corp = Corpus("data/C50train", 1)
query_corp

Corpus(data/C50train)

In [308]:
vec2 = Vector(query_corp.docs.iloc[0], corp)
vec2

Vector(data/C50train/KouroshKarimkhany/202658newsML.txt, corpus=data/C50test, query=False)

In [309]:
vec2.tf_idf

abandon      0.000000
abel         0.000000
abil         0.000000
absolut      0.000000
access       0.000000
               ...   
york         0.062323
yoshida      0.000000
yoshinobu    0.000000
yuan         0.000000
zinc         0.000000
Name: data/C50train/KouroshKarimkhany/202658newsML.txt, Length: 1744, dtype: float64

In [310]:
vec.tf_idf

abandon      0.0
abel         0.0
abil         0.0
absolut      0.0
access       0.0
            ... 
york         0.0
yoshida      0.0
yoshinobu    0.0
yuan         0.0
zinc         0.0
Name: data/C50test/EdnaFernandes/343315newsML.txt, Length: 1744, dtype: float64

In [216]:
tf_idf(temp, temp_words)

abandon      abat   abidjan  \
docname                                                                        
data/C50train/KarlPenhaul/217081newsML.txt      3.058894  4.643856  3.643856   
data/C50train/JoWinterbottom/210506newsML.txt   3.058894  4.643856  3.643856   
data/C50train/MatthewBunce/107670newsML.txt     3.058894  4.643856  3.670883   
data/C50train/BenjaminKangLim/222816newsML.txt  3.102372  4.643856  3.643856   
data/C50train/FumikoFujisaki/167905newsML.txt   3.058894  4.643856  3.643856   
data/C50train/MarcelMichelson/108487newsML.txt  3.058894  4.643856  3.643856   
data/C50train/BradDorfman/321585newsML.txt      3.058894  4.643856  3.643856   
data/C50train/GrahamEarnshaw/244929newsML.txt   3.058894  4.643856  3.643856   
data/C50train/LynneO'Donnell/27316newsML.txt    3.058894  4.643856  3.643856   
data/C50train/JanLopatka/254538newsML.txt       3.058894  4.643856  3.643856   
data/C50train/LynnleyBrowning/308394newsML.txt  3.058894  4.643856  3.643856   
data/C50train/PeterHumphrey/26410newsML.txt     3.058894  4.643856  3.643856   
data/C50train/SimonCowell/15627newsML.txt       3.088305  4.643856  3.643856   
data/C50train/NickLouth/133736newsML.txt        3.058894  4.643856  3.643856   
data/C50train/EdnaFernandes/17343newsML.txt     3.058894  4.643856  3.643856   
data/C50train/MatthewBunce/280201newsML.txt     3.058894  4.643856  3.834332   
data/C50train/WilliamKazer/208244newsML.txt     3.058894  4.643856  3.643856   
data/C50train/MarkBendeich/398974newsML.txt     3.089197  4.643856  3.643856   
data/C50train/TheresePoletti/243514newsML.txt   3.058894  4.643856  3.643856   
data/C50train/EricAuchard/139624newsML.txt      3.058894  4.643856  3.643856   
data/C50train/SarahDavison/213002newsML.txt     3.058894  4.676114  3.643856   
data/C50train/LynnleyBrowning/153131newsML.txt  3.058894  4.643856  3.643856   
data/C50train/PatriciaCommins/108222newsML.txt  3.058894  4.643856  3.643856   
data/C50train/BernardHickey/118470newsML.txt    3.058894  4.643856  3.643856   
data/C50train/PatriciaCommins/117099newsML.txt  3.058894  4.643856  3.643856   

                                                  abnorm    abroad  abruptli  \
docname                                                                        
data/C50train/KarlPenhaul/217081newsML.txt      4.643856  4.643856  4.643856   
data/C50train/JoWinterbottom/210506newsML.txt   4.643856  4.643856  4.643856   
data/C50train/MatthewBunce/107670newsML.txt     4.643856  4.643856  4.643856   
data/C50train/BenjaminKangLim/222816newsML.txt  4.643856  4.643856  4.643856   
data/C50train/FumikoFujisaki/167905newsML.txt   4.643856  4.643856  4.643856   
data/C50train/MarcelMichelson/108487newsML.txt  4.643856  4.643856  4.643856   
data/C50train/BradDorfman/321585newsML.txt      4.643856  4.643856  4.643856   
data/C50train/GrahamEarnshaw/244929newsML.txt   4.643856  4.643856  4.643856   
data/C50train/LynneO'Donnell/27316newsML.txt    4.643856  4.643856  4.643856   
data/C50train/JanLopatka/254538newsML.txt       4.643856  4.643856  4.643856   
data/C50train/LynnleyBrowning/308394newsML.txt  4.643856  4.643856  4.643856   
data/C50train/PeterHumphrey/26410newsML.txt     4.643856  4.643856  4.643856   
data/C50train/SimonCowell/15627newsML.txt       4.643856  4.643856  4.643856   
data/C50train/NickLouth/133736newsML.txt        4.643856  4.643856  4.643856   
data/C50train/EdnaFernandes/17343newsML.txt     4.643856  4.643856  4.643856   
data/C50train/MatthewBunce/280201newsML.txt     4.643856  4.643856  4.691475   
data/C50train/WilliamKazer/208244newsML.txt     4.643856  4.643856  4.643856   
data/C50train/MarkBendeich/398974newsML.txt     4.704462  4.643856  4.643856   
data/C50train/TheresePoletti/243514newsML.txt   4.643856  4.643856  4.643856   
data/C50train/EricAuchard/139624newsML.txt      4.643856  4.643856  4.643856   
data/C50train/SarahDavison/213002newsML.txt     4.643856  4.643856  4.643856   
data/C50train/LynnleyBrowning/153131newsML.txt  

In [318]:
vec.cos_sim(vec2)

0.6207284478988127

In [316]:
vec.okapi(vec2)

38.2519769942878

# HERE

In [2]:
import pandas as pd
import numpy as np
import json

from textVectorizer import *

In [2]:
corp1 = Corpus()
corp1.fit("data\C50train", size=25)
corp1

Corpus(data\C50train)

In [3]:
vecs = corp1.pull_all()
vecs

[Vector(data\C50train\AaronPressman\270084newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\JaneMacartney\249226newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\LynnleyBrowning\166151newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\ToddNissen\160059newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\TanEeLyn\155113newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\MarcelMichelson\144673newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\KouroshKarimkhany\172988newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\LynnleyBrowning\103703newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\TimFarrand\237957newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\LynneO'Donnell\20855newsML.txt, corpus=data\C50train, query=False),
 Vector(data\C50train\EdnaFernandes\207536newsML.txt, corpus=data\C50train, query=False),
 Vector(dat

In [4]:
vecs[0].author()

'AaronPressman'

In [3]:
corp1.to_json("sample_corpus.json")

'[\n {\n  "loc": "data/C50train/MureDickie/144988newsML.txt",\n  "corpus": "data/C50train",\n  "words": [\n   "abil",\n   "abn",\n   "abound",\n   "absenc",\n   "absolut",\n   "acceler",\n   "accept",\n   "access",\n   "accord",\n   "account",\n   "accus",\n   "achiev",\n   "acquir",\n   "acquisit",\n   "action",\n   "activist",\n   "activ",\n   "adam",\n   "add",\n   "ad",\n   "addit",\n   "address",\n   "adequ",\n   "adjac",\n   "admit",\n   "adorn",\n   "advantag",\n   "advisor",\n   "advisori",\n   "aeronautica",\n   "aerospac",\n   "aerospatial",\n   "affair",\n   "african",\n   "afternoon",\n   "ag",\n   "aggress",\n   "ago",\n   "agre",\n   "agreement",\n   "ahead",\n   "aid",\n   "aim",\n   "air",\n   "airbu",\n   "aircraft",\n   "airless",\n   "airlin",\n   "airport",\n   "airwav",\n   "akanuma",\n   "akishig",\n   "alabama",\n   "alain",\n   "alcatel",\n   "alex",\n   "allan",\n   "alleg",\n   "allianc",\n   "allow",\n   "alpha",\n   "alsthom",\n   "alta",\n   "alter",\n   "a

In [3]:
vec11 = corp1.pull(corp1.docs.iloc[0])
vec11

Vector(data/C50train/SimonCowell/376405newsML.txt, corpus=data/C50train, query=False)

In [5]:
vec11.tf_idf

abidjan      0.0
abn          0.0
abnorm       0.0
abnorn       0.0
abnornm      0.0
            ... 
yuan         0.0
yuchengco    0.0
zemin        0.0
zeneca       0.0
zoom         0.0
Name: data/C50train/SimonCowell/376405newsML.txt, Length: 1913, dtype: float64

In [4]:
corp1.docs.apply(lambda d: corp1.pull())

2221          data/C50train/SimonCowell/376405newsML.txt
483           data/C50train/EricAuchard/203838newsML.txt
1346            data/C50train/LydiaZajc/356565newsML.txt
2124         data/C50train/SarahDavison/324597newsML.txt
2189          data/C50train/ScottHillis/301673newsML.txt
2444           data/C50train/ToddNissen/280639newsML.txt
667         data/C50train/JaneMacartney/127969newsML.txt
582        data/C50train/GrahamEarnshaw/249198newsML.txt
906          data/C50train/JonathanBirt/124585newsML.txt
1282    data/C50train/KouroshKarimkhany/271894newsML.txt
1193          data/C50train/KevinMorrison/2730newsML.txt
804              data/C50train/JoeOrtiz/137871newsML.txt
2261             data/C50train/TanEeLyn/186184newsML.txt
505        data/C50train/FumikoFujisaki/132085newsML.txt
1163        data/C50train/KevinMorrison/176105newsML.txt
702             data/C50train/JanLopatka/10224newsML.txt
1295    data/C50train/KouroshKarimkhany/313088newsML.txt
11          data/C50train/Aaron

In [3]:
with open("data_vectorized.json", 'r') as file:
    vecs_dict = json.load(file)

In [4]:
vecs_in = pd.Series(vecs_dict).apply(vector_from_dict).tolist()
vecs_in

[Vector(data/C50test/LydiaZajc/426019newsML.txt, corpus=data, query=False),
 Vector(data/C50test/JoeOrtiz/415575newsML.txt, corpus=data, query=False),
 Vector(data/C50train/AlexanderSmith/237953newsML.txt, corpus=data, query=False),
 Vector(data/C50test/TheresePoletti/411582newsML.txt, corpus=data, query=False),
 Vector(data/C50test/PeterHumphrey/509680newsML.txt, corpus=data, query=False),
 Vector(data/C50test/KouroshKarimkhany/354282newsML.txt, corpus=data, query=False),
 Vector(data/C50test/DavidLawder/201827newsML.txt, corpus=data, query=False),
 Vector(data/C50train/FumikoFujisaki/167727newsML.txt, corpus=data, query=False),
 Vector(data/C50train/JoWinterbottom/131132newsML.txt, corpus=data, query=False),
 Vector(data/C50train/SamuelPerry/151392newsML.txt, corpus=data, query=False),
 Vector(data/C50test/LydiaZajc/387432newsML.txt, corpus=data, query=False),
 Vector(data/C50test/MureDickie/297664newsML.txt, corpus=data, query=False),
 Vector(data/C50train/KevinMorrison/125545newsML

In [7]:
vecs_in[0].name()

'426019newsML.txt'

In [14]:
def list_files_in_directory(directory):
    file_list = []
    for root, dirs, files in os.walk(directory):
        for file in files:
            file_list.append(os.path.join(root, file))
    return file_list

folder_path = 'data'
files = list_files_in_directory(folder_path)

for file in files:
    print(file)

data\C50test\BradDorfman\492830newsML.txt
data\C50test\BradDorfman\494048newsML.txt
data\C50test\BradDorfman\497821newsML.txt
data\C50test\BradDorfman\498878newsML.txt
data\C50test\BradDorfman\499850newsML.txt
data\C50test\BradDorfman\502697newsML.txt
data\C50test\BradDorfman\509785newsML.txt
data\C50test\BradDorfman\510133newsML.txt
data\C50test\BradDorfman\510134newsML.txt
data\C50test\BradDorfman\532261newsML.txt
data\C50test\BradDorfman\541677newsML.txt
data\C50test\BradDorfman\541918newsML.txt
data\C50test\BradDorfman\543949newsML.txt
data\C50test\BradDorfman\544122newsML.txt
data\C50test\BradDorfman\556131newsML.txt
data\C50test\BradDorfman\559756newsML.txt
data\C50test\DarrenSchuettler\392045newsML.txt
data\C50test\DarrenSchuettler\394766newsML.txt
data\C50test\DarrenSchuettler\409728newsML.txt
data\C50test\DarrenSchuettler\426024newsML.txt
data\C50test\DarrenSchuettler\431621newsML.txt
data\C50test\DarrenSchuettler\432674newsML.txt
data\C50test\DarrenSchuettler\43376newsML.txt
